<a href="https://colab.research.google.com/github/RapaDewan/Review_Scraping/blob/main/Modifying_Dataset_W_Bert(1)/Modifying_Dataset_1.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [1]:
import pandas as pd

In [2]:
all_app_rvw='https://raw.githubusercontent.com/amanullahshah32/Review-Scraping/refs/heads/main/Dataset/all_app_reviews.csv'
df=pd.read_csv(all_app_rvw)
df.head()

source                             review_id      user_name  \
0  Google Play  d33f5fbd-e904-4c35-a29d-9bf66d393aa1  A Google user   
1  Google Play  b1c90db8-c97e-401a-87db-f970ad5b7ce3  A Google user   
2  Google Play  fd85498c-702e-4bc7-8cde-70411670e214  A Google user   
3  Google Play  b8cc25c1-40c1-46d9-a238-bf0116de6ac4  A Google user   
4  Google Play  c0dfc093-493f-4906-80cb-1de222fbb02b  A Google user   

   review_title review_description  rating  thumbs_up          review_date  \
0           NaN               nice       5          0  2024-10-10 12:50:00   
1           NaN               good       5          0  2024-10-10 12:43:03   
2           NaN               good       5          0  2024-10-10 12:35:00   
3           NaN               good       5          0  2024-10-10 12:18:52   
4           NaN             good 😊       4          0  2024-10-10 11:39:51   

  developer_response developer_response_date appVersion language_code  \
0                NaN                     NaN        NaN            en   
1                NaN                     NaN      2.1.8            en   
2                NaN                     NaN      2.1.8            en   
3                NaN                     NaN      2.1.8            en   
4                NaN                     NaN      2.1.8            en   

  country_code        app_name  
0           us  com.twgbd.dims  
1           us  com.twgbd.dims  
2           us  com.twgbd.dims  
3           us  com.twgbd.dims  
4           us  com.twgbd.dims

In [3]:
df.shape

(99395, 14)

#Applying BERT Analysis

#Dependencies

In [18]:
import numpy as np
!pip install torch==1.8.1+cu111 torchvision==0.9.1+cu111 torchaudio===0.8.1 -f https://download.pytorch.org/whl/torch_stable.html
!pip install transformers requests beautifulsoup4 pandas numpy
from transformers import AutoTokenizer, AutoModelForSequenceClassification
import torch
import requests
from bs4 import BeautifulSoup
import re

Looking in links: https://download.pytorch.org/whl/torch_stable.html
ERROR: Could not find a version that satisfies the requirement torch==1.8.1+cu111 (from versions: 1.11.0, 1.11.0+cpu, 1.11.0+cu102, 1.11.0+cu113, 1.11.0+cu115, 1.11.0+rocm4.3.1, 1.11.0+rocm4.5.2, 1.12.0, 1.12.0+cpu, 1.12.0+cu102, 1.12.0+cu113, 1.12.0+cu116, 1.12.0+rocm5.0, 1.12.0+rocm5.1.1, 1.12.1, 1.12.1+cpu, 1.12.1+cu102, 1.12.1+cu113, 1.12.1+cu116, 1.12.1+rocm5.0, 1.12.1+rocm5.1.1, 1.13.0, 1.13.0+cpu, 1.13.0+cu116, 1.13.0+cu117, 1.13.0+cu117.with.pypi.cudnn, 1.13.0+rocm5.1.1, 1.13.0+rocm5.2, 1.13.1, 1.13.1+cpu, 1.13.1+cu116, 1.13.1+cu117, 1.13.1+cu117.with.pypi.cudnn, 1.13.1+rocm5.1.1, 1.13.1+rocm5.2, 2.0.0, 2.0.0+cpu, 2.0.0+cpu.cxx11.abi, 2.0.0+cu117, 2.0.0+cu117.with.pypi.cudnn, 2.0.0+cu118, 2.0.0+rocm5.3, 2.0.0+rocm5.4.2, 2.0.1, 2.0.1+cpu, 2.0.1+cpu.cxx11.abi, 2.0.1+cu117, 2.0.1+cu117.with.pypi.cudnn, 2.0.1+cu118, 2.0.1+rocm5.3, 2.0.1+rocm5.4.2, 2.1.0, 2.1.0+cpu, 2.1.0+cpu.cxx11.abi, 2.1.0+cu118, 2.1.0+cu121, 2.

#Model

In [19]:
tokenizer=AutoTokenizer.from_pretrained('nlptown/bert-base-multilingual-uncased-sentiment')
model=AutoModelForSequenceClassification.from_pretrained('nlptown/bert-base-multilingual-uncased-sentiment')

/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_token.py:89: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


tokenizer_config.json:   0%|          | 0.00/39.0 [00:00<?, ?B/s]

config.json:   0%|          | 0.00/953 [00:00<?, ?B/s]

vocab.txt:   0%|          | 0.00/872k [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/112 [00:00<?, ?B/s]

/usr/local/lib/python3.10/dist-packages/transformers/tokenization_utils_base.py:1601: FutureWarning: `clean_up_tokenization_spaces` was not set. It will be set to `True` by default. This behavior will be depracted in transformers v4.45, and will be then set to `False` by default. For more details check this issue: https://github.com/huggingface/transformers/issues/31884
  warnings.warn(


pytorch_model.bin:   0%|          | 0.00/669M [00:00<?, ?B/s]

In [4]:
df_rvw_desc = df[['review_description']]
df_rvw_desc.head()

review_description
0               nice
1               good
2               good
3               good
4             good 😊

In [5]:
df_rvw_desc.shape

(99395, 1)

In [12]:
# Convert the 'review_description' column into a list of strings
reviews_list = df_rvw_desc['review_description'].dropna().tolist()

# Display the formatted list
print(reviews_list)


['nice', 'good', 'good', 'good', 'good 😊', 'Pharmaceutical', 'Fahim', 'good', 'good', 'The apps useful. Best service', 'ok', 'good', 'md zahirul islam', 'very interestin', 'good apps', 'very nice app', 'Nice', 'good apps', 'good 😊', 'nice', 'good', 'good', 'fine', 'There is no full version of the system l think in next additions you may include full version of this device', 'Effective for everyone ❤️', 'good', 'beautiful', 'Very good', 'অনেক উপকারী একটি অ্যাপ', 'very useful aap', 'very helpful', 'Excellent', '❤️', 'Good', 'best', 'good', 'good', 'excellent', 'Nice', 'good', 'best app', 'It’s very interesting app', 'Excellent apps for medical professionals', 'lots of new drugs are missing,u guys should update.', '👍', 'Good apps', 'good', 'It is a great app for a mdeicin sels man, i like it very much', 'good', 'Good.', 'you have to update it with time.', 'awesome 💯💯💯💯', 'Good App', 'very good', 'good', 'good', 'Nc Apps', 'vary nicely done.', 'help full app', 'good', 'ok', 'very much help

In [13]:
df= pd.DataFrame(np.array(reviews_list), columns=['review'])

In [14]:
df['review'].iloc[0]

'nice'

In [21]:
def sentiment_score(review):
    tokens = tokenizer.encode(review, return_tensors='pt')
    result = model(tokens)
    return int(torch.argmax(result.logits))+1

In [22]:
sentiment_score(df['review'].iloc[0])

4

In [25]:
##df['sentiment'] = df['review'].apply(lambda x: sentiment_score(x[:512]))